In [3]:
'''!pip install pandas'''

'!pip install pandas'

In [4]:
import pandas as pd
import numpy as np
from turfpy.measurement import boolean_point_in_polygon,points_within_polygon
from geojson import Point, Polygon, Feature, FeatureCollection


In [5]:
df1  = pd.read_csv("rides-january-2019.csv")
#df1.head()

In [6]:
'''c = df1["moving_time(HH:MM:SS)"].dtype
df1.info()'''

'c = df1["moving_time(HH:MM:SS)"].dtype\ndf1.info()'

In [7]:
df1["seconds"] = [int(t.split(":")[0]) * 3600 + int(t.split(":")[1]) * 60 + int(t.split(":")[2])
                 for t in df1["moving_time(HH:MM:SS)"]]


In [8]:
df1["speed"]=(df1["distance(m)"]//df1["seconds"])*3.6
#df1.head()

In [9]:
Q1 = df1["speed"].quantile(0.25)
Q3 = df1["speed"].quantile(0.75)
IQR = Q3-Q1
upper_bound=Q3+1.5*IQR
df1 = df1[(df1["speed"] >= Q1) & (df1["speed"] <= upper_bound)]

In [68]:
upper_bound

28.799999999999997

In [10]:

#df1.sort_values("moving_time(HH:MM:SS)", ascending=False)
df1.drop(columns=["seconds"])


start_date(DD/MM/YYYY HH:MM:SS)  distance(m) moving_time(HH:MM:SS)  \
0                01/01/2019 01:12:55      15558.1              00:51:37   
1                01/01/2019 01:25:55      11654.0              00:39:14   
2                01/01/2019 01:33:11       4012.0              00:21:09   
4                01/01/2019 02:31:43      11599.7              00:35:42   
5                01/01/2019 02:34:03      14632.4              00:42:55   
...                              ...          ...                   ...   
3722             31/01/2019 16:09:48      12383.0              00:42:20   
3723             31/01/2019 16:27:51       8058.1              00:28:29   
3724             31/01/2019 16:38:33       4623.7              00:22:07   
3725             31/01/2019 16:40:00       7009.8              00:24:15   
3726             31/01/2019 16:59:11       7373.3              00:27:47   

                                                  route  speed  
0     [[20.28302, 72.99185], [20.28249, 72.99185], [...   18.0  
1     [[12.96455, 77.53573], [12.96847, 77.53762], [...   14.4  
2     [[11.08677, 77.0059], [11.08678, 77.00578], [1...   10.8  
4     [[13.05943, 77.5042], [13.06023, 77.50468], [1...   18.0  
5     [[12.89456, 77.58772], [12.89502, 77.588180000...   18.0  
...                                                 ...    ...  
3722  [[12.9357, 77.61282], [12.936710000000001, 77....   14.4  
3723  [[12.93331, 77.69513], [12.932780000000001, 77...   14.4  
3724  [[14.55799, 121.01757], [14.55884, 121.0177700...   10.8  
3725  [[12.99303, 77.70651], [12.992849999999999, 77...   14.4  
3726  [[12.91918, 77.68426], [12.919270000000001, 77...   14.4  

[3566 rows x 5 columns]

In [11]:
import ast
df1["route"] = [ast.literal_eval(t) for t in df1["route"]]


In [12]:
df1["no_route_coordinates"] = [len(t) for t in df1["route"]]
'''p = df1[df1.no_route_coordinates==df1.no_route_coordinates.max()]["route"]
len(p)
for i in p:
    print(i[0])
df1'''

'p = df1[df1.no_route_coordinates==df1.no_route_coordinates.max()]["route"]\nlen(p)\nfor i in p:\n    print(i[0])\ndf1'

In [13]:
import random

In [14]:
#df1.head()
def reduce_coordinates(arr):
    ar=[(i, a) for i, a in enumerate(arr)]
    mid=len(ar)//2
    arr1= ar[:mid]
    arr2=ar[mid+1:][::-1] if len(ar)%2!=0 else ar[mid:][::-1] 
    q2 = []
    q2.append(arr1[0])
    q2.append(arr2[0])
    q2.append(ar[mid] if len(ar)%2!=0 else ar[mid-1])
    generated_numbers = []
    def generate_random_number(start, end, generated_numbers):
        number = random.randint(start, end)

        if number in generated_numbers:
            return generate_random_number(start, end, generated_numbers)
        generated_numbers.append(number)
        return number
    while len(q2)<10:
        new = generate_random_number(1,len(arr1)-2,generated_numbers)
        q2.append(arr1[new])
        q2.append(arr2[new])
    return [i[1] for i in sorted(q2)]
    

In [15]:

df1["new_route"] = df1.route.map(lambda x: reduce_coordinates(x) if len(x)>20 else x)

In [16]:
df1["no_route_coordinates"] = [len(t) for t in df1["new_route"]]


In [17]:
'''routes2 = [{"features":[{"type":"Feature","properties": {"title": "new","description": "new"},"geometry": {"coordinates": j[::-1],"type": "Point"},} for i in p for j in i],"type": "FeatureCollection"}]'''


'routes2 = [{"features":[{"type":"Feature","properties": {"title": "new","description": "new"},"geometry": {"coordinates": j[::-1],"type": "Point"},} for i in p for j in i],"type": "FeatureCollection"}]'

In [18]:
'''import json
json_string = json.dumps(routes2)'''

'import json\njson_string = json.dumps(routes2)'

In [19]:
'''with open("routes2.geojson", "w") as file:
    file.write(json_string)'''

'with open("routes2.geojson", "w") as file:\n    file.write(json_string)'

In [20]:
'''routes3 = {"locations":[{"lat":rot[i][0],"lon":rot[i][1],"type":"break"} for i in range(0, len(rot))],"costing":"auto","costing_options":"auto","directions_options":{"units":"miles"}}
json_string = json.dumps(routes3)'''

'routes3 = {"locations":[{"lat":rot[i][0],"lon":rot[i][1],"type":"break"} for i in range(0, len(rot))],"costing":"auto","costing_options":"auto","directions_options":{"units":"miles"}}\njson_string = json.dumps(routes3)'

In [21]:
'''with open("routes.txt", "w") as file:
    file.write("-j '"+json_string+"'")'''

'with open("routes.txt", "w") as file:\n    file.write("-j \'"+json_string+"\'")'

In [22]:
rot = [i for i in df1["new_route"]]
rot2 = [rot[i] for i in range(100)]
#rot2

In [23]:
df1["no_route_coordinates"] = [len(t) for t in df1["route"]]
'''df1.head()'''

'df1.head()'

In [24]:
df1["avg_time"]=df1["seconds"]/df1["no_route_coordinates"]
'''df1.head()'''

'df1.head()'

In [25]:
df1["avg_distance"]=df1["distance(m)"]/df1["no_route_coordinates"]
'''df1.head()'''

'df1.head()'

In [26]:
import json
df2 = pd.read_json("bangalore_wards_new.json")
'''df2'''

'df2'

In [27]:
with open('bangalore_wards_new.json','r') as f:
    data = json.loads(f.read())
df_nested_list = pd.json_normalize(data, record_path =['features'])
'''df_nested_list'''

'df_nested_list'

In [28]:
def resize(ward_coord):
    a = np.array(ward_coord, dtype=object)
    b = a.shape
    a.resize(b[len(b)-2],2)
    return a

In [29]:
df_nested_list["resized"]=[resize(i) for i in df_nested_list["geometry.coordinates"]]
'''df_nested_list'''

'df_nested_list'

In [30]:
'''%pip install turfpy
%pip install geojson'''

'%pip install turfpy\n%pip install geojson'

In [31]:
def convert_coord(coord):
    point = Feature(geometry=Point((coord[1],coord[0])))
    return point
def convert_ward(ward):
    polygon = Polygon([[(i[0],i[1]) for i in ward]])
    return polygon
def check_if_point_in_ward(coord, ward):
    return boolean_point_in_polygon(coord, ward)

In [32]:
converted_wards = [convert_ward(ward) for ward in df_nested_list["resized"]]

In [33]:
'''ward_mat = []
def ward_array(route):
    arr = [0]* len(route)
    route_coord = [convert_coord(coord) for coord in route]
    print(route_coord[0])
    for i,a in enumerate(route_coord):
        for j, b in enumerate(converted_wards):
            print(b["coordinates"][0][0])
            if boolean_point_in_polygon(a,b):
                arr[i] = df_nested_list["properties.WARD_NO"][j]
                break
    return arr
ward_mat=[ward_array(route) for route in df1["route"]]
ward_mat'''

'ward_mat = []\ndef ward_array(route):\n    arr = [0]* len(route)\n    route_coord = [convert_coord(coord) for coord in route]\n    print(route_coord[0])\n    for i,a in enumerate(route_coord):\n        for j, b in enumerate(converted_wards):\n            print(b["coordinates"][0][0])\n            if boolean_point_in_polygon(a,b):\n                arr[i] = df_nested_list["properties.WARD_NO"][j]\n                break\n    return arr\nward_mat=[ward_array(route) for route in df1["route"]]\nward_mat'

In [34]:
'''%pip install geopandas
%pip install shapely'''

'%pip install geopandas\n%pip install shapely'

In [35]:
import geopandas as gpd
import matplotlib.pyplot as plt
from shapely.geometry import Point

In [36]:
'''df = pd.DataFrame({'lon':lon, 'lat':lat})
df['coords'] = list(zip(df['lon'],df['lat']))
df.head()'''

"df = pd.DataFrame({'lon':lon, 'lat':lat})\ndf['coords'] = list(zip(df['lon'],df['lat']))\ndf.head()"

In [37]:
rot = [j for i in df1["route"] for j in i]
lat = [k[0] for k in rot]
lon = [k[1] for k in rot]
lat = np.array(lat)
lon = np.array(lon)
lat, lon

(array([20.28302, 20.28249, 20.2829 , ..., 12.95464, 12.95411, 12.95525]),
 array([72.99185, 72.99185, 72.99372, ..., 77.69067, 77.69048, 77.69246]))

In [38]:
df_coord_data = pd.DataFrame({'lon':lon, 'lat':lat})
df_coord_data['coords'] = list(zip(df_coord_data['lon'],df_coord_data['lat']))

In [39]:
df_coord_data['coords'] = df_coord_data['coords'].apply(Point)
wards = gpd.GeoDataFrame.from_file('./mygeodata/bangalore_wards_new-polygon.shp')
points = gpd.GeoDataFrame(df_coord_data, geometry='coords', crs=wards.crs)

In [40]:
pointInPolys = gpd.tools.sjoin(points, wards, predicate="within", how='left')

In [41]:
'''base = wards.boundary.plot(linewidth=1, edgecolor="black")
pnt_LA = points[pointInPolys.WARD_NO=='3']
pnt_LA.plot(ax=base, linewidth=1, color="red", markersize=1)
plt.show()'''

'base = wards.boundary.plot(linewidth=1, edgecolor="black")\npnt_LA = points[pointInPolys.WARD_NO==\'3\']\npnt_LA.plot(ax=base, linewidth=1, color="red", markersize=1)\nplt.show()'

In [42]:
pnt_ward_mat = [points[pointInPolys.WARD_NO==str(i)] for i in range(1,199)]

In [43]:
'''for i in pnt_ward_mat[0].itertuples():
    print(i.lat, i.lon)'''
matr = []
for i in pnt_ward_mat:
    mat = []
    for j in i.itertuples():
        mat.append([j.lat, j.lon])
    matr.append(mat)

    

In [44]:
def od_matrix(route, avg_time, avg_dist):
    mat = []
    for i in range(len(route)):
        sub_mat = [[0,0]for j in range(len(route))]
        l=r=i
        while l>=0:
            sub_mat[l][0] = abs(l-i)*avg_time
            sub_mat[l][1] = abs(l-i)*avg_dist
            l-=1
        while r<len(route):            
            sub_mat[r][0] = abs(r-i)*avg_time
            sub_mat[r][1] = abs(r-i)*avg_dist
            r+=1
        mat.append(sub_mat)
    return mat



In [45]:
a = [od_matrix(i.route, i.avg_time, i.avg_distance) for i in df1.itertuples()]
#a

In [46]:
df1["od_matrix"] = a
'''df1.head()'''

'df1.head()'

In [47]:
def return_ward(coord):
    for i, a in enumerate(matr):
        if coord in a:
            return i+1
    return None

In [48]:
e = []
for i in df1["route"]:
    mat = []
    for j in i:
        mat.append(return_ward(j))
    e.append(mat)


In [49]:
df1["ward_arr"] = e


In [50]:
def add_ward_to_od(od, ward):
    for i in od:
        for j in i:
            k = i.index(j)
            j.append(ward[k])
    return od

new_od_matrix = [add_ward_to_od(i.od_matrix, i.ward_arr) for i in df1.itertuples()]

In [51]:
df1["new_od_matrix"] = new_od_matrix

In [52]:
df1.drop(columns=["new_od_matrix"],axis=1, inplace=True)
#df1.head()

In [53]:
from collections import defaultdict
hmap2 = defaultdict(lambda: defaultdict(int))
for i in range(1,199):
    hmap2[i]

In [54]:
e = [i.copy() for i in df1["od_matrix"]]
for p,i in enumerate(e):
    for q, j in enumerate(i):
        e[p][q] = sorted(j,key=lambda x: x[0])



In [55]:
df1["od_matrix"] = e
'''df1.head()'''

'df1.head()'

In [56]:
'''a = set()
def add_to_hashmap(odmat):
    for j in odmat:
        for k in range(1, len(j)):
            if j[0][2]!=None and j[k][2]!=None and j[k][2] != j[0][2]:
                if j[k][2] not in a:
                    hmap[j[0][2]].append(j[k])
                    a.add(j[k][2])
                else:
                    if j[k][2] in [i for i in hmap[j[0][2]]]:
                        for m in range(len(hmap[j[0][2]])):
                            if j[k][2] == hmap[j[0][2]][m][2]:
                                hmap[j[0][2]][m][0] = (hmap[j[0][2]][m][0]+j[k][0])
                                hmap[j[0][2]][m][1] = (hmap[j[0][2]][m][1]+j[k][1])
                    else:
                        hmap[j[0][2]].append(j[k])'''

'a = set()\ndef add_to_hashmap(odmat):\n    for j in odmat:\n        for k in range(1, len(j)):\n            if j[0][2]!=None and j[k][2]!=None and j[k][2] != j[0][2]:\n                if j[k][2] not in a:\n                    hmap[j[0][2]].append(j[k])\n                    a.add(j[k][2])\n                else:\n                    if j[k][2] in [i for i in hmap[j[0][2]]]:\n                        for m in range(len(hmap[j[0][2]])):\n                            if j[k][2] == hmap[j[0][2]][m][2]:\n                                hmap[j[0][2]][m][0] = (hmap[j[0][2]][m][0]+j[k][0])\n                                hmap[j[0][2]][m][1] = (hmap[j[0][2]][m][1]+j[k][1])\n                    else:\n                        hmap[j[0][2]].append(j[k])'

In [57]:
'''for i in df1["od_matrix"]:
    add_to_hashmap(i)'''
'''hmap'''

'hmap'

In [58]:
hmap2

defaultdict(<function __main__.<lambda>()>,
            {1: defaultdict(int, {}),
             2: defaultdict(int, {}),
             3: defaultdict(int, {}),
             4: defaultdict(int, {}),
             5: defaultdict(int, {}),
             6: defaultdict(int, {}),
             7: defaultdict(int, {}),
             8: defaultdict(int, {}),
             9: defaultdict(int, {}),
             10: defaultdict(int, {}),
             11: defaultdict(int, {}),
             12: defaultdict(int, {}),
             13: defaultdict(int, {}),
             14: defaultdict(int, {}),
             15: defaultdict(int, {}),
             16: defaultdict(int, {}),
             17: defaultdict(int, {}),
             18: defaultdict(int, {}),
             19: defaultdict(int, {}),
             20: defaultdict(int, {}),
             21: defaultdict(int, {}),
             22: defaultdict(int, {}),
             23: defaultdict(int, {}),
             24: defaultdict(int, {}),
             25: defaultdict(

In [59]:
hmap = {}
for i in range(1,199):
    hmap[i] = {}

In [60]:
for key in hmap:
    for i in range(1,199):
        hmap[key][i]=[0,0]
hmap

{1: {1: [0, 0],
  2: [0, 0],
  3: [0, 0],
  4: [0, 0],
  5: [0, 0],
  6: [0, 0],
  7: [0, 0],
  8: [0, 0],
  9: [0, 0],
  10: [0, 0],
  11: [0, 0],
  12: [0, 0],
  13: [0, 0],
  14: [0, 0],
  15: [0, 0],
  16: [0, 0],
  17: [0, 0],
  18: [0, 0],
  19: [0, 0],
  20: [0, 0],
  21: [0, 0],
  22: [0, 0],
  23: [0, 0],
  24: [0, 0],
  25: [0, 0],
  26: [0, 0],
  27: [0, 0],
  28: [0, 0],
  29: [0, 0],
  30: [0, 0],
  31: [0, 0],
  32: [0, 0],
  33: [0, 0],
  34: [0, 0],
  35: [0, 0],
  36: [0, 0],
  37: [0, 0],
  38: [0, 0],
  39: [0, 0],
  40: [0, 0],
  41: [0, 0],
  42: [0, 0],
  43: [0, 0],
  44: [0, 0],
  45: [0, 0],
  46: [0, 0],
  47: [0, 0],
  48: [0, 0],
  49: [0, 0],
  50: [0, 0],
  51: [0, 0],
  52: [0, 0],
  53: [0, 0],
  54: [0, 0],
  55: [0, 0],
  56: [0, 0],
  57: [0, 0],
  58: [0, 0],
  59: [0, 0],
  60: [0, 0],
  61: [0, 0],
  62: [0, 0],
  63: [0, 0],
  64: [0, 0],
  65: [0, 0],
  66: [0, 0],
  67: [0, 0],
  68: [0, 0],
  69: [0, 0],
  70: [0, 0],
  71: [0, 0],
  72: [0, 0]

In [61]:
def add_to_hashmap(odmat):
    for i,a in enumerate(odmat):
        if odmat[i][0][2]!=None:
            for k in range(1, len(a)):
                if odmat[i][k][2]!=odmat[i][0][2] and odmat[i][k][2]!=None:
                    hmap[odmat[i][0][2]][odmat[i][k][2]][0] += odmat[i][k][0]
                    hmap[odmat[i][0][2]][odmat[i][k][2]][1] += odmat[i][k][1]

    

In [62]:
for i in df1["od_matrix"]:
    add_to_hashmap(i)
hmap

{1: {1: [0, 0],
  2: [126941.72276679848, 828692.935111456],
  3: [329035.8671146244, 2104567.497382332],
  4: [20439.160724637684, 129029.9664868875],
  5: [0, 0],
  6: [3840.0176991150443, 17655.203539823007],
  7: [22843.734513274336, 112109.34690265486],
  8: [1818.9557522123894, 8362.991150442478],
  9: [0, 0],
  10: [0, 0],
  11: [0, 0],
  12: [0, 0],
  13: [0, 0],
  14: [0, 0],
  15: [0, 0],
  16: [0, 0],
  17: [0, 0],
  18: [0, 0],
  19: [0, 0],
  20: [4506.888888888889, 23396.306666666664],
  21: [3976.666666666666, 20643.800000000003],
  22: [0, 0],
  23: [3435.8053097345132, 15796.761061946903],
  24: [4244.230088495575, 19513.646017699117],
  25: [0, 0],
  26: [0, 0],
  27: [10509.522123893805, 48319.50442477877],
  28: [0, 0],
  29: [4648.442477876106, 21372.088495575223],
  30: [0, 0],
  31: [0, 0],
  32: [0, 0],
  33: [0, 0],
  34: [5037.11111111111, 26148.81333333333],
  35: [0, 0],
  36: [0, 0],
  37: [0, 0],
  38: [0, 0],
  39: [0, 0],
  40: [0, 0],
  41: [0, 0],
  42

In [63]:
def add_to_hashmap2(odmat):
    for i,a in enumerate(odmat):
        if odmat[i][0][2]!=None:
            for k in range(1, len(a)):
                if odmat[i][k][2]!=odmat[i][0][2] and odmat[i][k][2]!=None:
                    hmap2[odmat[i][0][2]][odmat[i][k][2]] = 1 + hmap2[odmat[i][0][2]].get(odmat[i][k][2],0)

In [64]:
for i in df1["od_matrix"]:
    add_to_hashmap2(i)

hmap2

defaultdict(<function __main__.<lambda>()>,
            {1: defaultdict(int,
                         {4: 61,
                          3: 385,
                          2: 231,
                          7: 32,
                          8: 2,
                          23: 2,
                          6: 2,
                          24: 2,
                          29: 2,
                          27: 4,
                          50: 4,
                          56: 6,
                          55: 2,
                          79: 2,
                          112: 4,
                          114: 6,
                          148: 2,
                          151: 22,
                          21: 4,
                          20: 4,
                          34: 4,
                          64: 4,
                          93: 8,
                          110: 20,
                          111: 28,
                          117: 16,
                          147: 12,
                   

In [65]:
for k, v in hmap2.items():
    for l, n in v.items():
        hmap[k][l][0] = round(hmap[k][l][0]/hmap2[k][l])
        hmap[k][l][1] = round(hmap[k][l][1]/hmap2[k][l])
hmap

{1: {1: [0, 0],
  2: [550, 3587],
  3: [855, 5466],
  4: [335, 2115],
  5: [0, 0],
  6: [1920, 8828],
  7: [714, 3503],
  8: [909, 4181],
  9: [0, 0],
  10: [0, 0],
  11: [0, 0],
  12: [0, 0],
  13: [0, 0],
  14: [0, 0],
  15: [0, 0],
  16: [0, 0],
  17: [0, 0],
  18: [0, 0],
  19: [0, 0],
  20: [1127, 5849],
  21: [994, 5161],
  22: [0, 0],
  23: [1718, 7898],
  24: [2122, 9757],
  25: [0, 0],
  26: [0, 0],
  27: [2627, 12080],
  28: [0, 0],
  29: [2324, 10686],
  30: [0, 0],
  31: [0, 0],
  32: [0, 0],
  33: [0, 0],
  34: [1259, 6537],
  35: [0, 0],
  36: [0, 0],
  37: [0, 0],
  38: [0, 0],
  39: [0, 0],
  40: [0, 0],
  41: [0, 0],
  42: [0, 0],
  43: [0, 0],
  44: [0, 0],
  45: [0, 0],
  46: [0, 0],
  47: [0, 0],
  48: [0, 0],
  49: [0, 0],
  50: [3436, 15797],
  51: [0, 0],
  52: [0, 0],
  53: [0, 0],
  54: [0, 0],
  55: [3537, 16261],
  56: [3402, 15642],
  57: [0, 0],
  58: [0, 0],
  59: [0, 0],
  60: [0, 0],
  61: [0, 0],
  62: [0, 0],
  63: [0, 0],
  64: [1392, 7225],
  65: [0,

In [66]:
api_made = [{"origin_id": str(k), "destinations": [{str(l):{"time":str(n[0]),"distance":str(n[1])}} for l, n in v.items()]} for k,v in hmap.items()]
api_made   

[{'origin_id': '1',
  'destinations': [{'1': {'time': '0', 'distance': '0'}},
   {'2': {'time': '550', 'distance': '3587'}},
   {'3': {'time': '855', 'distance': '5466'}},
   {'4': {'time': '335', 'distance': '2115'}},
   {'5': {'time': '0', 'distance': '0'}},
   {'6': {'time': '1920', 'distance': '8828'}},
   {'7': {'time': '714', 'distance': '3503'}},
   {'8': {'time': '909', 'distance': '4181'}},
   {'9': {'time': '0', 'distance': '0'}},
   {'10': {'time': '0', 'distance': '0'}},
   {'11': {'time': '0', 'distance': '0'}},
   {'12': {'time': '0', 'distance': '0'}},
   {'13': {'time': '0', 'distance': '0'}},
   {'14': {'time': '0', 'distance': '0'}},
   {'15': {'time': '0', 'distance': '0'}},
   {'16': {'time': '0', 'distance': '0'}},
   {'17': {'time': '0', 'distance': '0'}},
   {'18': {'time': '0', 'distance': '0'}},
   {'19': {'time': '0', 'distance': '0'}},
   {'20': {'time': '1127', 'distance': '5849'}},
   {'21': {'time': '994', 'distance': '5161'}},
   {'22': {'time': '0', 'dis

In [67]:
b = []
for k, v in hmap2.items():
    if len(v)==0:
        b.append(k)
b

[5,
 13,
 32,
 33,
 36,
 37,
 42,
 43,
 47,
 48,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 99,
 100,
 101,
 102,
 103,
 107,
 126,
 127,
 141]